In [1]:
import deconV as dv
import scout

import glob, tqdm, time, os
import torch
import matplotlib
import matplotlib.pyplot as plt
from matplotlib import rcParams


import pandas as pd
import numpy as np
import scanpy as sc
import scvi
import seaborn as sns
import tqdm
import scout

import plotly.graph_objects as go
import plotly.express as px

%load_ext autoreload
%autoreload 2

Global seed set to 0


In [2]:
params = {
    "cell_type_key": "cellType",
    "fig_fmt": "png",

    "selected_ct": ["0", "1", "2"],
    "bulk_file": "../../data/GSE136148/bulk.tsv",
    "ref_annot_file": "../../data/GSE136148/pdata.tsv",
    "ref_file": "../../data/GSE136148/sc.tsv",
    
    "outdir": "out",
    "figsize": (8,8),
    "dpi": 80,
}

sc.settings.set_figure_params(dpi=80, facecolor='white')
plt.rc("patch", edgecolor="black", facecolor="royalblue", linewidth=1.0)
plt.rc("axes", facecolor="white", edgecolor="black", linewidth=1.0)

sc.settings.verbosity = 0

In [3]:
sadata = dv.tl.read_data(params["ref_file"])
print(f"scRNA-seq data - cells: {sadata.shape[0]}, genes: {sadata.shape[1]}")

scRNA-seq data - cells: 3022, genes: 33694


In [4]:
print("Reading pheno data...")
pheno_df = pd.read_csv(params["ref_annot_file"], sep="\t", index_col=0)
pheno_df.index.name = None

Reading pheno data...


In [5]:
common_cells = list(set(pheno_df.index.tolist()) & set(sadata.obs_names.tolist()))
len(common_cells)

3022

In [6]:
sadata = sadata[common_cells, :].copy()
pheno_df = pheno_df.loc[common_cells, :].copy()
sadata.obs[params["cell_type_key"]] = pheno_df[params["cell_type_key"]].tolist()
sadata.obs.groupby(params["cell_type_key"]).size()

cellType
0    1988
1     686
2     319
3      29
dtype: int64

In [7]:
print("Reading bulk data...")
bulk_df = pd.read_csv(params["bulk_file"], sep="\t", index_col=None)
if bulk_df.iloc[:,0].dtype == "O":
    bulk_df.set_index(bulk_df.columns[0], inplace=True)
print(f"bulk RNA-seq data - samples: {bulk_df.shape[0]}, genes: {bulk_df.shape[1]}")

Reading bulk data...
bulk RNA-seq data - samples: 1, genes: 58387


In [8]:
if params["selected_ct"] is not None and len(params["selected_ct"]) > 0:
    sadata = sadata[sadata.obs[params["cell_type_key"]].astype("str").isin(params["selected_ct"]), :].copy()

sadata.obs[params["cell_type_key"]] = sadata.obs[params["cell_type_key"]].astype("category")
sadata.obs.groupby(params["cell_type_key"]).size()

cellType
0    1988
1     686
2     319
dtype: int64

In [9]:
sc.pp.filter_cells(sadata, min_genes=200)
sc.pp.filter_genes(sadata, min_cells=3)
adata = dv.tl.combine(sadata, bulk_df)
scout.tl.scale_log_center(adata, target_sum=None, exclude_highly_expressed=True)

scRNA-seq data - cells: 2993, genes: 18597
bulk RNA-seq data - samples: 1, genes: 18597


In [10]:
adata.obs["super_type"] = adata.obs["cellType"].isin([1, 2]).astype("category")

In [11]:
# sc.pp.neighbors(adata)
# sc.tl.umap(adata)
# scout.ply.projection(adata, hue="super_type")

In [12]:
decon = dv.DeconV(adata, cell_type_key="cellType", sub_type_key=None, layer="counts")

In [13]:
# decon.filter_outliers(dropout_factor_quantile=0.9, pseudobulk_lims=(-np.inf, np.inf), aggregate="max") # 0.9 (-10, 10)

In [14]:
decon.init_dataset(
    weight_type=None, weight_agg="max",
    inverse_weight=False, log_weight=False,
    quantiles=(0, 1) #0,1
)

In [15]:
res = decon.deconvolute(
    model_type="lrm",
    num_epochs=1000,
    lr=0.1,
    use_outlier_genes=False,
    progress_bar=True,
    signature_quantiles=(0, 1.0), # 0,0.9
    log_loss=True
)
res

100%|██████████| 1000/1000 [00:01<00:00, 764.76it/s, proportions=0.36 0.40 0.24, lib_size=3349.3, loss=39927.7]


array([[0.36145529, 0.40078652, 0.23775819]])

In [16]:
def prediction_plot(adata, res, i):
    mu, _ = decon.get_signature()
    est_bulk = np.log1p(torch.sum(mu * res[0, :] * 3537.8, dim=1).numpy())
    true_bulk = np.log1p(adata.varm["bulk"][:, i])

    _max = max(est_bulk.max(), true_bulk.max())
    mask = np.ones(len(est_bulk), dtype=bool)
    # mask = (bulk == 0)

    clr = adata.varm["pseudo_factor"][:, i][mask]
    zmin = clr.min()
    zmax = clr.max()
    zcenter = (0 - zmin) / (zmax - zmin)

    f = px.scatter(
        x=np.log1p(mu[mask].mean(1)),
        y=true_bulk[mask]-est_bulk[mask],
        log_x=False, log_y=False,
        # color=np.log1p(adata.varm["cv_cellType"].max(1))[mask],
        color=clr,
        color_continuous_scale=scout.ply.colors.seismic(zcenter),
        # trendline="ols",
    )
    f.update_layout(
        width=800, height=500,
        xaxis_title="log1p(mean gene expression)",
        yaxis_title="log1p(bulk) - log1p(est bulk)",
    )

    # f.add_trace(
    #     go.Scatter(x=[0, _max], y=[0, _max], mode="lines", line=dict(dash="dash"))
    # )
    return f

In [17]:
prediction_plot(adata, res, 0)


In [18]:
prediction_plot(adata, res, 0)

In [19]:
x = np.log1p(adata.varm["pseudo"][:, 0])
# x = x / x.sum()
y = np.log1p(adata.varm["bulk"][:, 0])
# y = y / y.sum()
px.scatter(
    x=x,
    y=y,
)

In [20]:
# est_bulk = np.log1p(np.sum(adata.varm["mu_expression_cellType"] * [0.6, 0.3, 0.1] * 3277, axis=1))
est_bulk = np.log1p(np.sum(adata.varm["mu_expression_cellType"] * lrm.get_counts().detach().numpy(), axis=1))
true_bulk = np.log1p(adata.varm["bulk"][:, 0])

mu = adata.X.mean(0)
pf = adata.varm["pseudo_factor"][:, 0]
dist = true_bulk - est_bulk

f = px.scatter(
    x=mu,
    y=dist,
    color=adata.varm["gene_weights"],
    hover_name=adata.var_names,
)
f
# f.add_trace(
#     go.Scatter(x=[x.min(), x.max()], y=[y.min(), y.max()], mode="lines", line=dict(dash="dash"))
# )

KeyError: 'mu_expression_cellType'